In [1]:
from sys import path
path.insert(0,'../python')
from zip_codes_to_coordinates import *
from stop_clustering import *
from graph_making import *
import json

In [3]:
import pandas as pd

## Obtaining the associates zipcodes
(1. - Zipcodes to Coordinates)

In [4]:
aguascalientes_plant = [21.967103, -102.284380]

In [5]:
#open the file with the zipcodes
associates = pd.read_excel('../../data/aguascalientes/example.xlsx',dtype=str)
associates_columns = associates.columns.tolist()
#check the format of the zipcodes
check_zipcode_format(associates, cp_column = 'Cód.postal')
#merge the zipcodes with the coordinates database
associates = merge_coordinates(associates,cp_column = 'Cód.postal')
#filtering coordinates
bounds = [  [21.611472417139705,-102.87322998046875],
            [21.611472417139705,-101.65924072265625],
            [22.550610920226646,-101.65924072265625],
            [ 22.550610920226646,-102.87322998046875],
            [21.611472417139705,-102.87322998046875]]

filter_coordinates(associates, bounds)

NameError: name 'check_zipcode_format' is not defined

In [4]:
associates.loc[associates.has_coords].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 730 entries, 0 to 735
Data columns (total 10 columns):
Nº pers.              730 non-null object
Número de personal    730 non-null object
Cód.postal            730 non-null object
good_zip_code         730 non-null bool
CP                    730 non-null object
lat                   730 non-null float64
lon                   730 non-null float64
address               730 non-null object
has_coords            730 non-null bool
in_bounds             730 non-null bool
dtypes: bool(3), float64(2), object(5)
memory usage: 47.8+ KB


In [5]:
tiles_url = 'https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png'
attrb ='&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>'
m = folium.Map(tiles=None)

folium.TileLayer(tiles_url,attr=attrb,name = 'Mapeo de Asociados Aguascalientes', show = True).add_to(m)

text = '<h4>Planta Bosch Aguascalientes</h4>'
text = folium.Html(text, script=True)
popup = folium.Popup(text, max_width=2650)
folium.Marker(aguascalientes_plant, icon = folium.Icon(color='red'), popup=popup).add_to(m)


table = associates.loc[associates.in_bounds]

zip_codes_lyr = get_associates_zip_codes_layer(table, show = True)
fast_cluster_lyr = get_associates_cluster_layer(table)
heatmap_lyr = get_associates_heatmap_layer(table)

zip_codes_lyr.add_to(m)

fast_cluster_lyr.add_to(m)
#heatmap_lyr.add_to(m)

table = associates.loc[associates.has_coords]
pt_lyr = folium.FeatureGroup(name = 'Heatmap', show=False)
pt_lyr.add_child(HeatMap(table[['lat', 'lon']].astype(float).values, max_val = 1))
pt_lyr.add_to(m)

Fullscreen(position='topleft', title='Full Screen', title_cancel='Exit Full Screen', force_separate_button=False).add_to(m)
folium.LayerControl(collapsed=False).add_to(m)
m.fit_bounds(m.get_bounds())
m
#m.save('../maps/Mapeo Asociados Aguascalientes.html')

In [6]:
heatmap_lyr

### Filter the zip codes coordinates

In [7]:
filter_coordinates(associates, bounds)
filter_associates = associates.loc[associates.in_bounds]
fliter_coords = filter_associates[['lat','lon']].values

grouped_zipcodes = group_zip_codes(associates)
filter_coordinates(grouped_zipcodes, bounds)
filter_associates = grouped_zipcodes.loc[grouped_zipcodes.in_bounds]
fliter_coords = filter_associates[['lat','lon']].values

### Obtaining the current routes of the plants 

2 .- Stop clustering

### Defining parameters

In [8]:
distance = 1000
min_samples = 5

In [9]:
with open('../../data/aguascalientes/routes_polylines_ags.json') as json_file:
    routes = json.load(json_file)
    
stops = get_all_stops(routes)
good_stops = get_good_stops(stops)

In [10]:
dispersed_zip_codes = disperse_coords(filter_associates,max_radius = 750)

clusters,clusters_coincidence = get_associates_clusters(dispersed_zip_codes, get_stops_coords(good_stops), distance, min_samples)

In [11]:
covered_associates, not_covered_associates = get_coverage(np.asarray(clusters_coincidence), dispersed_zip_codes)

In [12]:
len(clusters)

72

In [13]:
tiles_url = 'https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png'
attrb ='&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>'
m = folium.Map(tiles=None)

folium.TileLayer(tiles_url,attr=attrb,name = 'Mapeo Asociados Toluca', show = True).add_to(m)
 

    

cluster_lyr = folium.FeatureGroup(name = 'Cluster algorithm',show=False)

for i, point in enumerate(clusters):
    folium.Marker(point, icon = folium.Icon(color = 'red')).add_to(cluster_lyr)  

for i, point in enumerate(not_covered_associates):
    folium.CircleMarker(point,radius = 4,
                    
                    fill=True, # Set fill to True|
                    fill_color='white',
                    color = 'gray',
                    fill_opacity=1).add_to(cluster_lyr)
    
    
for i, point in enumerate(covered_associates):
    folium.CircleMarker(point,radius = 4,
                    
                    fill=True, # Set fill to True|
                    fill_color='white',
                    color = 'green',
                    fill_opacity=1).add_to(cluster_lyr)
    
zip_codes_lyr.add_to(m)
fast_cluster_lyr.add_to(m)
heatmap_lyr.add_to(m)
cluster_lyr.add_to(m)

Fullscreen(position='topleft', title='Full Screen', title_cancel='Exit Full Screen', force_separate_button=False).add_to(m)
folium.LayerControl(collapsed=False).add_to(m)
m.fit_bounds(m.get_bounds())
m
#m.save('Maps/Rutas Sugeridas Urbvan Monterrey.html')

## Graph making

In [14]:
destination = aguascalientes_plant
stop_coords = clusters
stop_weights = [len(con) for con in clusters_coincidence]

In [15]:
 ## Creating the graph
graph = Graph(stop_coords, 
              destination, 
              stop_weights, 
              n = 8, 
              include_dest = False, 
              edge_func = 'wide', 
              request_matrix=True,
              w_weights = 1, 
              w_end_distance = 1, 
              w_edge_distance = 1)

graph.cut_edges()

Requesting...
Request made!


In [16]:
import folium
from folium.plugins import MarkerCluster,HeatMap, Fullscreen
from folium import plugins

tiles_url = 'https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png'
attrb ='&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>'
m = folium.Map(tiles=None)

folium.TileLayer(tiles_url,attr=attrb,name = 'Mapeo Asociados Toluca', show = True).add_to(m)

folium.Marker(destination, icon = folium.Icon(color='red')).add_to(m) 

graph_lyr = folium.FeatureGroup(name = 'Connections Graph',show=False)

for i in range(len(graph.edges)):
    for j in range(len(graph.edges)):
        if graph.edges[i,j] != np.inf:
            node = graph.node[i]
            nd = graph.node[j]
            text = f'<p>{format_distance(graph.edges[i,j])}</p>'
            text = folium.Html(text, script=True)
            popup = folium.Popup(text, max_width=2650)
            popup = create_edge_table(graph,i,j)
            folium.PolyLine([[node.x, node.y], [nd.x, nd.y]], popup=popup, color = 'red').add_to(graph_lyr)
            
for i in range(len(graph.edges)):
    node = graph.node[i]
    folium.CircleMarker([node.x, node.y],radius = 4, popup=i,
                        fill=True, # Set fill to True|
                        fill_color='white',
                        color = 'blue',
                        fill_opacity=1).add_to(graph_lyr)  
    
graph_lyr.add_to(m)
            

Fullscreen(position='topleft', title='Full Screen', title_cancel='Exit Full Screen', force_separate_button=False).add_to(m)
folium.LayerControl(collapsed=False).add_to(m)
m.fit_bounds(m.get_bounds())
m
#m.save('Maps/Rutas Sugeridas Urbvan Monterrey.html')

## Route optimization

In [18]:
tiles_url = 'https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png'
attrb ='&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>'
m = folium.Map(tiles=None)

folium.TileLayer(tiles_url,attr=attrb,name = 'Mapeo de Asociados Aguascalientes', show = True).add_to(m)

text = '<h4>Planta Bosch Aguascalientes</h4>'
text = folium.Html(text, script=True)
popup = folium.Popup(text, max_width=2650)
folium.Marker(aguascalientes_plant, icon = folium.Icon(color='red'), popup=popup).add_to(m)


table = associates.loc[associates.in_bounds]

get_associates_zip_codes_layer(table, show = True).add_to(m)
get_associates_cluster_layer(table).add_to(m)
get_associates_heatmap_layer(table).add_to(m)


pt_lyr = folium.FeatureGroup(name = 'Cluster algorithm',show=False)

for i, point in enumerate(clusters):
    folium.Marker(point, icon = folium.Icon(color = 'red')).add_to(pt_lyr)  

for i, point in enumerate(not_covered_associates):
    folium.CircleMarker(point,radius = 4,
                    
                    fill=True, # Set fill to True|
                    fill_color='white',
                    color = 'gray',
                    fill_opacity=1).add_to(pt_lyr)
    
    
for i, point in enumerate(covered_associates):
    folium.CircleMarker(point,radius = 4,
                    
                    fill=True, # Set fill to True|
                    fill_color='white',
                    color = 'green',
                    fill_opacity=1).add_to(pt_lyr)

pt_lyr.add_to(m)

graph_lyr.add_to(m)

Fullscreen(position='topleft', title='Full Screen', title_cancel='Exit Full Screen', force_separate_button=False).add_to(m)
folium.LayerControl(collapsed=False).add_to(m)
m.fit_bounds(m.get_bounds())
m
#m.save('../maps/Mapeo Asociados Aguascalientes.html')